In [1]:
from absl import logging

import tensorflow as tf
import tensorflow_hub as hub
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import re
import seaborn as sns
import tensorflow as tf
import tensorflow_hub.tf_v1

model = tensorflow_hub.tf_v1.saved_model.load_v2("/Users/onijinsky/Downloads/", tags=['serve'])
def embed(input):
    return model(input)

In [2]:
def get_sentence_new(content, beg, end):
    original_beg = beg
    original_end = end    
    while not content[beg:end].endswith('.') and end != len(content):
        end += 1
    while not content[beg:end].startswith('.') and beg != 0:
        beg -= 1
    sentences = content[beg:end]
    return sentences, original_beg - beg, original_end - end

In [3]:
import pandas as pd

yago_df = pd.read_csv('yago_2020.csv')
yago_df['index'] = range(yago_df.shape[0])

In [4]:
def get_locs(string_locs):
    import re
    locations = string_locs
    locations = re.sub('\[', '', locations)
    locations = re.sub('\]', '', locations)
    locations = re.sub('\(', '', locations)
    locations = re.sub('\)', '', locations)
    locations = re.sub('\s+', '', locations)
    int_locs = [int(x) for x in locations.split(',') if len(x) > 0]
    tuple_locs = []
    for i in range(0, len(int_locs), 2):
        tuple_locs.append((int_locs[i], int_locs[i + 1]))
    return tuple_locs

# Positive 

In [5]:
import xml.etree.ElementTree as ET
import pandas as pd
import numpy as np
import itertools
import spacy
from IPython.display import clear_output

tmp = None
start = None
finish = None

text_a = list()
text_b = list()
mention_a = list()
mention_b = list()
entity_id_a = list()
entity_id_b = list()
same_entity = list()
db_entity_a = list()
db_entity_b = list()
a_vec = list()
b_vec = list()
a_sen_vec = list()
b_sen_vec = list()
a_sen = list()
b_sen = list()
a_text = list()
b_text = list()
a_beg_end = list()
b_beg_end = list()

for name, group in yago_df.groupby(['id']):
#     group = group.drop_duplicates(subset='mention', keep='first')
    for index_a, row_a in group.iterrows():
        for index_b, row_b in group.iterrows():
            if row_a['mention'] != row_b['mention']:
                continue
                
            # a
            text_a.append(row_a['entity'])
            mention_a.append(row_a['mention'])
            entity_id_a.append(row_a['id'])
            a_vec.append(embed([row_a['mention']]))
            a_text.append(row_a['context'])
            a_beg_end.append(row_a['mention_location'])
            
            locations = row_a['mention_location']
            tuple_int_locs = get_locs(locations)
            tmp_sent_vec_a = 0.0
            for loc in tuple_int_locs:
                sent_a = get_sentence_new(row_a['context'], loc[0], loc[1])
                tmp_sent_vec_a += embed([sent_a[0]])
            if len(tuple_int_locs) != 0:
                avg_sen_sim_a = tmp_sent_vec_a / len(tuple_int_locs)
            else:
                avg_sen_sim_a = [0] * 512
            a_sen_vec.append(avg_sen_sim_a)
            a_sen.append(row_a['context'])
            
            # b
            text_b.append(row_b['entity'])
            mention_b.append(row_b['mention'])
            entity_id_b.append(row_b['id'])
            b_vec.append(embed([row_b['mention']])[0])
            b_text.append(row_b['context'])
            b_beg_end.append(row_b['mention_location'])
            
            locations = row_b['mention_location']
            tuple_int_locs = get_locs(locations)
            tmp_sent_vec_b = 0.0
            for loc in tuple_int_locs:
                tmp = row_b['context']
                start = loc[0]
                finish = loc[1]
                sent_b = get_sentence_new(row_b['context'], loc[0], loc[1])
                tmp_sent_vec_b += embed([sent_b[0]])
            if len(tuple_int_locs) != 0:
                avg_sen_sim_b = tmp_sent_vec_b / len(tuple_int_locs)
            else:
                avg_sen_sim_b = [0] * 512
            b_sen_vec.append(avg_sen_sim_b)
            b_sen.append(row_b['context'])
                        
            if row_a['entity'] == row_b['entity']:
                same_entity.append(1)
            else:
                same_entity.append(0)
            
            db_entity_a.append(row_a['entity'])
            db_entity_b.append(row_b['entity'])
            
positive_dataset = pd.DataFrame({'text_a': text_a,
                                 'text_b': text_b,
                                 'mention_a': mention_a,
                                 'mention_b': mention_b,
                                 'entity_id_a': entity_id_a,
                                 'entity_id_b': entity_id_b,
                                 'same_entity': same_entity,
                                 'kb_entity_a': db_entity_a,
                                 'kb_entity_b': db_entity_b,
                                 'a_word_vec': a_vec,
                                 'b_word_vec': b_vec,
                                 'a_sen_vec': a_sen_vec,
                                 'b_sen_vec': b_sen_vec,
                                 'a_sen': a_sen,
                                 'b_sen': b_sen,
                                 'all_text_a': a_text,
                                 'a_word_loc': a_beg_end,
                                 'all_text_b': b_text,
                                 'b_word_loc': b_beg_end
                                 })

positive_dataset.to_csv('yago_positive_pairs_trivials.csv')

KeyboardInterrupt: 

In [11]:
positive_dataset = pd.DataFrame({'text_a': text_a[:497283],
                                 'text_b': text_b[:497283],
                                 'mention_a': mention_a[:497283],
                                 'mention_b': mention_b[:497283],
                                 'entity_id_a': entity_id_a[:497283],
                                 'entity_id_b': entity_id_b[:497283],
                                 'same_entity': same_entity[:497283],
                                 'kb_entity_a': db_entity_a[:497283],
                                 'kb_entity_b': db_entity_b[:497283],
                                 'a_word_vec': a_vec[:497283],
                                 'b_word_vec': b_vec[:497283],
                                 'a_sen_vec': a_sen_vec[:497283],
                                 'b_sen_vec': b_sen_vec[:497283],
                                 'a_sen': a_sen[:497283],
                                 'b_sen': b_sen[:497283],
                                 'all_text_a': a_text[:497283],
                                 'a_word_loc': a_beg_end[:497283],
                                 'all_text_b': b_text[:497283],
                                 'b_word_loc': b_beg_end[:497283]
                                 })

positive_dataset.to_csv('yago_positive_pairs_trivials.csv')

KeyboardInterrupt: 

# Negative

In [13]:
import xml.etree.ElementTree as ET
import pandas as pd
import numpy as np
import itertools
import spacy
from IPython.display import clear_output

tmp = None
start = None
finish = None

text_a = list()
text_b = list()
mention_a = list()
mention_b = list()
entity_id_a = list()
entity_id_b = list()
same_entity = list()
db_entity_a = list()
db_entity_b = list()
a_vec = list()
b_vec = list()
a_sen_vec = list()
b_sen_vec = list()
a_sen = list()
b_sen = list()
a_text = list()
b_text = list()
a_beg_end = list()
b_beg_end = list()

for name, group in yago_df.groupby(['mention']):
#     group = group.drop_duplicates(subset='id', keep='first')
    for index_a, row_a in group.iterrows():
        for index_b, row_b in group.iterrows():
            if row_a['entity'] == row_b['entity']:
                continue

            # a
            text_a.append(row_a['entity'])
            mention_a.append(row_a['mention'])
            entity_id_a.append(row_a['id'])
            a_vec.append(embed([row_a['mention']]))
            a_text.append(row_a['context'])
            a_beg_end.append(row_a['mention_location'])
            
            locations = row_a['mention_location']
            tuple_int_locs = get_locs(locations)
            tmp_sent_vec_a = 0.0
            for loc in tuple_int_locs:
                sent_a = get_sentence_new(row_a['context'], loc[0], loc[1])
                tmp_sent_vec_a += embed([sent_a[0]])
            if len(tuple_int_locs) != 0:
                avg_sen_sim_a = tmp_sent_vec_a / len(tuple_int_locs)
            else:
                avg_sen_sim_a = [0] * 512
            a_sen_vec.append(avg_sen_sim_a)
            a_sen.append(row_a['context'])
            
            # b
            text_b.append(row_b['entity'])
            mention_b.append(row_b['mention'])
            entity_id_b.append(row_b['id'])
            b_vec.append(embed([row_b['mention']])[0])
            b_text.append(row_b['context'])
            b_beg_end.append(row_b['mention_location'])
            
            locations = row_b['mention_location']
            tuple_int_locs = get_locs(locations)
            tmp_sent_vec_b = 0.0
            for loc in tuple_int_locs:
                tmp = row_b['context']
                start = loc[0]
                finish = loc[1]
                sent_b = get_sentence_new(row_b['context'], loc[0], loc[1])
                tmp_sent_vec_b += embed([sent_b[0]])
            if len(tuple_int_locs) != 0:
                avg_sen_sim_b = tmp_sent_vec_b / len(tuple_int_locs)
            else:
                avg_sen_sim_b = [0] * 512
            b_sen_vec.append(avg_sen_sim_b)
            b_sen.append(row_b['context'])
                        
            if row_a['entity'] == row_b['entity']:
                same_entity.append(1)
            else:
                same_entity.append(0)
            
            db_entity_a.append(row_a['entity'])
            db_entity_b.append(row_b['entity'])
            
positive_dataset = pd.DataFrame({'text_a': text_a,
                                 'text_b': text_b,
                                 'mention_a': mention_a,
                                 'mention_b': mention_b,
                                 'entity_id_a': entity_id_a,
                                 'entity_id_b': entity_id_b,
                                 'same_entity': same_entity,
                                 'kb_entity_a': db_entity_a,
                                 'kb_entity_b': db_entity_b,
                                 'a_word_vec': a_vec,
                                 'b_word_vec': b_vec,
                                 'a_sen_vec': a_sen_vec,
                                 'b_sen_vec': b_sen_vec,
                                 'a_sen': a_sen,
                                 'b_sen': b_sen,
                                 'all_text_a': a_text,
                                 'a_word_loc': a_beg_end,
                                 'all_text_b': b_text,
                                 'b_word_loc': b_beg_end
                                 })

positive_dataset.to_csv('yago_negative_pairs_not_trivials.csv')

KeyboardInterrupt: 

In [15]:
positive_dataset = pd.DataFrame({'text_a': text_a[:316074],
                                 'text_b': text_b[:316074],
                                 'mention_a': mention_a[:316074],
                                 'mention_b': mention_b[:316074],
                                 'entity_id_a': entity_id_a[:316074],
                                 'entity_id_b': entity_id_b[:316074],
                                 'same_entity': same_entity[:316074],
                                 'kb_entity_a': db_entity_a[:316074],
                                 'kb_entity_b': db_entity_b[:316074],
                                 'a_word_vec': a_vec[:316074],
                                 'b_word_vec': b_vec[:316074],
                                 'a_sen_vec': a_sen_vec[:316074],
                                 'b_sen_vec': b_sen_vec[:316074],
                                 'a_sen': a_sen[:316074],
                                 'b_sen': b_sen[:316074],
                                 'all_text_a': a_text[:316074],
                                 'a_word_loc': a_beg_end[:316074],
                                 'all_text_b': b_text[:316074],
                                 'b_word_loc': b_beg_end[:316074]
                                 })

positive_dataset.to_csv('yago_negative_pairs_not_trivials.csv')

In [16]:
pd.read_csv('yago_positive_pairs_trivials.csv').head(10)

Unnamed: 0                                        text_a  \
0           0          http://en.wikipedia.org/wiki/Alabama   
1           1          http://en.wikipedia.org/wiki/Alabama   
2           2          http://en.wikipedia.org/wiki/Alabama   
3           3          http://en.wikipedia.org/wiki/Alabama   
4           4  http://en.wikipedia.org/wiki/Abraham_Lincoln   
5           5  http://en.wikipedia.org/wiki/Abraham_Lincoln   
6           6  http://en.wikipedia.org/wiki/Abraham_Lincoln   
7           7  http://en.wikipedia.org/wiki/Abraham_Lincoln   
8           8  http://en.wikipedia.org/wiki/Abraham_Lincoln   
9           9  http://en.wikipedia.org/wiki/Abraham_Lincoln   

                                         text_b        mention_a  \
0          http://en.wikipedia.org/wiki/Alabama              Ala   
1          http://en.wikipedia.org/wiki/Alabama              Ala   
2          http://en.wikipedia.org/wiki/Alabama              Ala   
3          http://en.wikipedia.org/wiki/Alabama              Ala   
4  http://en.wikipedia.org/wiki/Abraham_Lincoln  Abraham Lincoln   
5  http://en.wikipedia.org/wiki/Abraham_Lincoln  Abraham Lincoln   
6  http://en.wikipedia.org/wiki/Abraham_Lincoln  Abraham Lincoln   
7  http://en.wikipedia.org/wiki/Abraham_Lincoln  Abraham Lincoln   
8  http://en.wikipedia.org/wiki/Abraham_Lincoln          Lincoln   
9  http://en.wikipedia.org/wiki/Abraham_Lincoln          Lincoln   

         mention_b  entity_id_a  entity_id_b  same_entity  \
0              Ala        303.0        303.0            1   
1              Ala        303.0        303.0            1   
2              Ala        303.0        303.0            1   
3              Ala        303.0        303.0            1   
4  Abraham Lincoln        307.0        307.0            1   
5  Abraham Lincoln        307.0        307.0            1   
6  Abraham Lincoln        307.0        307.0            1   
7  Abraham Lincoln        307.0        307.0            1   
8          Lincoln        307.0        307.0            1   
9          Lincoln        307.0        307.0            1   

                                    kb_entity_a  \
0          http://en.wikipedia.org/wiki/Alabama   
1          http://en.wikipedia.org/wiki/Alabama   
2          http://en.wikipedia.org/wiki/Alabama   
3          http://en.wikipedia.org/wiki/Alabama   
4  http://en.wikipedia.org/wiki/Abraham_Lincoln   
5  http://en.wikipedia.org/wiki/Abraham_Lincoln   
6  http://en.wikipedia.org/wiki/Abraham_Lincoln   
7  http://en.wikipedia.org/wiki/Abraham_Lincoln   
8  http://en.wikipedia.org/wiki/Abraham_Lincoln   
9  http://en.wikipedia.org/wiki/Abraham_Lincoln   

                                    kb_entity_b  \
0          http://en.wikipedia.org/wiki/Alabama   
1          http://en.wikipedia.org/wiki/Alabama   
2          http://en.wikipedia.org/wiki/Alabama   
3          http://en.wikipedia.org/wiki/Alabama   
4  http://en.wikipedia.org/wiki/Abraham_Lincoln   
5  http://en.wikipedia.org/wiki/Abraham_Lincoln   
6  http://en.wikipedia.org/wiki/Abraham_Lincoln   
7  http://en.wikipedia.org/wiki/Abraham_Lincoln   
8  http://en.wikipedia.org/wiki/Abraham_Lincoln   
9  http://en.wikipedia.org/wiki/Abraham_Lincoln   

                                          a_word_vec  \
0  tf.Tensor(\n[[-0.01003989  0.06266098  0.02211...   
1  tf.Tensor(\n[[-0.01003989  0.06266098  0.02211...   
2  tf.Tensor(\n[[-0.01003989  0.06266098  0.02211...   
3  tf.Tensor(\n[[-0.01003989  0.06266098  0.02211...   
4  tf.Tensor(\n[[-0.0178345  -0.05129487  0.06849...   
5  tf.Tensor(\n[[-0.0178345  -0.05129487  0.06849...   
6  tf.Tensor(\n[[-0.0178345  -0.05129487  0.06849...   
7  tf.Tensor(\n[[-0.0178345  -0.05129487  0.06849...   
8  tf.Tensor(\n[[ 7.74836587e-03 -4.57403958e-02 ...   
9  tf.Tensor(\n[[ 7.74836587e-03 -4.57403958e-02 ...   

                                          b_word_vec  \
0  tf.Tensor(\n[-0.01003989  0.06266098  0.022115...   
1  tf.Tensor(\n[-0.01003989  0.0626

In [17]:
text_a = list()
text_b = list()
mention_a = list()
mention_b = list()
entity_id_a = list()
entity_id_b = list()
same_entity = list()
db_entity_a = list()
db_entity_b = list()
a_vec = list()
b_vec = list()
a_sen_vec = list()
b_sen_vec = list()
a_text = list()
a_beg_end = list()
b_text = list()
b_beg_end = list()
pos_trivial = pd.read_csv('yago_positive_pairs_trivials.csv')
pos_trivial = pos_trivial.drop_duplicates(subset=['mention_a', 'mention_b'], keep="first")
pos_trivial_tmp = pos_trivial
for i, x in pos_trivial.iterrows():
    for j, y in pos_trivial_tmp.drop(pos_trivial.index[0]).iterrows():
        if x['entity_id_a'] == y['entity_id_a'] or x['mention_a'] == y['mention_a']:
            continue
        
        print(x['mention_a'])
        print(y['mention_a'])
        print('************')
        text_a.append(x['text_a'])
        mention_a.append(x['mention_a'])
        entity_id_a.append(x['entity_id_a'])
        db_entity_a.append(x['kb_entity_a'])
        a_vec.append(x['a_word_vec'])
        a_sen_vec.append(x['a_sen_vec'])
        a_text.append(x['all_text_a'])
        a_beg_end.append(x['a_word_loc'])
        
        text_b.append(y['text_b'])
        mention_b.append(y['mention_b'])
        entity_id_b.append(y['entity_id_b'])
        db_entity_b.append(y['kb_entity_b'])
        b_vec.append(y['b_word_vec'])
        b_sen_vec.append(y['b_sen_vec'])
        b_text.append(y['all_text_b'])
        b_beg_end.append(y['b_word_loc'])
        
        same_entity.append(0)

negative_trivial_dataset = pd.DataFrame()
negative_trivial_dataset['text_a'] = text_a
negative_trivial_dataset['text_b'] = text_b
negative_trivial_dataset['mention_a'] = mention_a
negative_trivial_dataset['mention_b'] = mention_b
negative_trivial_dataset['entity_id_a'] = entity_id_a
negative_trivial_dataset['mention_b'] = mention_b
negative_trivial_dataset['same_entity'] = same_entity
negative_trivial_dataset['kb_entity_a'] = db_entity_a
negative_trivial_dataset['kb_entity_b'] = db_entity_b
negative_trivial_dataset['a_word_vec'] = a_vec
negative_trivial_dataset['b_word_vec'] = b_vec
negative_trivial_dataset['a_sen_vec'] = a_sen_vec
negative_trivial_dataset['b_sen_vec'] = b_sen_vec
negative_trivial_dataset['all_text_a'] =  a_text
negative_trivial_dataset['a_word_loc'] =  a_beg_end
negative_trivial_dataset['all_text_b'] = b_text
negative_trivial_dataset['b_word_loc'] =  b_beg_end
        
negative_trivial_dataset.to_csv('yago_negative_pairs_trivials.csv')

ERROR! Session/line number was not unique in database. History logging moved to new session 552
Ala
Abraham Lincoln
************
Ala
Lincoln
************
Ala
Academy Award-winning
************
Ala
Oscars
************
Ala
Algerian
************
Ala
Algeria
************
Ala
Algerians
************
Ala
Algiers
************
Ala
Andre Agassi
************
Ala
Agassi
************
Ala
Alaska
************
Ala
ASIA
************
Ala
Asia
************
Ala
Asian
************
Ala
ANGOLA
************
Ala
Angolan
************
Ala
Angola
************
Ala
Alberta
************
Ala
Afghan
************
Ala
Afghanistan
************
Ala
Afghans
************
Ala
Albania
************
Ala
Albanian
************
Ala
Allahu
************
Ala
Allah
************
Ala
Azerbaijan
************
Ala
Azeris
************
Ala
Azerbaijani
************
Ala
Azeri
************
Ala
ANKARA
************
Ala
Ankara
************
Ala
Arabic
************
Ala
AMSTERDAM
************
Ala
Amsterdam
************
Ala
Audi
************
Ala
Audi 